In [ ]:
! pip install bertopic embedding-atlas

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 153.0/153.0 kB 10.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.8/24.8 MB 60.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 70.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.0/4.0 MB 70.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.7/84.7 kB 8.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 124.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 99.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 65.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 15.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9

In [ ]:
from bertopic import BERTopic
import pandas as pd
from bs4 import BeautifulSoup

import plotly.io as pio
pio.renderers.default = "colab"

def html_cleaner(text):
    soup = BeautifulSoup(text,'html')
    return soup.text

In [ ]:

df = pd.read_parquet('filtered_cleaned_articles.parquet')
from sklearn.feature_extraction.text import CountVectorizer

cv = CountVectorizer(min_df=5, max_df=0.95, stop_words='english',ngram_range=(1,2))


In [ ]:
corpus = df['body'].apply(html_cleaner).tolist()
df['corpus'] = corpus

In [ ]:
from pathlib import Path
import numpy as np

embeds_path = Path('embeddings.npy')

if embeds_path.exists():
  embeddings = np.load(embeds_path)
else:
  from sentence_transformers import SentenceTransformer

  transformer = SentenceTransformer("all-MiniLM-L6-v2")
  embeddings = transformer.encode(corpus)
  np.save(embeds_path, embeddings)

In [ ]:
model_path = Path('my_model.pkl')
if model_path.exists():
  topic_model = BERTopic.load(model_path)
else:
  topic_model = BERTopic(calculate_probabilities=True, vectorizer_model=cv)
  topic_model.fit_transform(corpus, embeddings=embeddings)
  topic_model.save(model_path, serialization='pickle')

In [ ]:
from embedding_atlas.widget import EmbeddingAtlasWidget


In [ ]:
df['topic'] = [topic_model.topic_labels_[x] for x in topic_model.topics_]

In [ ]:
from embedding_atlas.projection import compute_text_projection

compute_text_projection(df, text="corpus",
    x="projection_x", y="projection_y", neighbors="neighbors"
)

In [ ]:
widget = EmbeddingAtlasWidget(df, text="corpus",
    x="projection_x", y="projection_y", neighbors="neighbors"
)
widget

EmbeddingAtlasWidget()

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.datasets import fetch_20newsgroups

cats = ('alt.atheism','sci.space','sci.electronics','soc.religion.christian')

ng_data = fetch_20newsgroups(remove=('headers','footers','quotes'), categories=cats, subset='all')
df = pd.DataFrame(ng_data['data'], columns=['text'])
df['label'] = ng_data.target

label_lookup = {i:name for i, name in enumerate(ng_data.target_names)}
df['label_text'] = df['label'].map(label_lookup)
df







text  label  \
0     \nDo you know of the world-wide-web?  This is ...      2   
1                                                            2   
2     A related question (which I haven't given that...      2   
3     \nRobin Lane Fox is a historian and a gardener...      3   
4     \nHello net.  I have a 386sx motherboard with ...      1   
...                                                 ...    ...   
3762  There is a nice little tool in Lucid emacs. It...      2   
3763  \nPerhaps we have different definitions of abs...      3   
3764  \n\n\nNo. I estimate a 99 % probability the Ge...      2   
3765  \n\nIf you want parallels the best source is p...      3   
3766  \nBill, ever heard of secular humanism? Please...      0   

                  label_text  
0                  sci.space  
1                  sci.space  
2                  sci.space  
3     soc.religion.christian  
4            sci.electronics  
...                      ...  
3762               sci.space  
3763  soc.religion.christian  
3764               sci.space  
3765  soc.religion.christian  
3766             alt.atheism  

[3767 rows x 3 columns]

In [ ]:
from sklearn.decomposition import PCA
tfidf = TfidfVectorizer(min_df=5, max_df=0.95, stop_words='english', ngram_range=(1,2))

X = tfidf.fit_transform(df['text'])
pca = PCA(2)
components = pca.fit_transform(X)

In [67]:
df['pca_x'] = components[:,0]
df['pca_y'] = components[:,1]
widget = EmbeddingAtlasWidget(df, text="text",
    x="pca_x", y="pca_y", neighbors="neighbors"
)
widget

EmbeddingAtlasWidget()

In [ ]:
widget.

EmbeddingAtlasWidget()

In [ ]:
widget.selection()

id      type  \
0   business/article/2024/aug/02/uk-funding-techno...   article   
1   business/article/2024/jul/12/british-chipmaker...   article   
2   commentisfree/article/2024/jul/10/rachel-reeve...   article   
3   business/article/2024/aug/04/a-simple-solution...   article   
4   business/article/2024/sep/01/germany-economy-p...   article   
5   business/article/2024/may/30/business-manifest...   article   
6   business/nils-pratley-on-finance/article/2024/...   article   
7   business/2024/feb/07/sainsburys-does-not-rule-...   article   
8   business/article/2024/jul/21/uk-services-based...   article   
9   technology/2023/may/20/labour-should-pledge-11...   article   
10  business/article/2024/jul/25/lloyds-bank-defau...   article   
11  australia-news/article/2024/may/14/australia-f...   article   
12  business/article/2024/jul/25/british-gas-profi...   article   
13  business/article/2024/jul/25/anglo-american-ta...   article   
14  business/article/2024/jun/25/uk-winemaker-chap...   article   
15  business/article/2024/jul/31/taylor-wimpey-lab...   article   
16  business/live/2024/jun/06/us-antitrust-inquiri...  liveblog   
17  business/article/2024/jul/09/rachel-reeves-nat...   article   
18  business/live/2024/sep/05/royal-mail-must-impr...  liveblog   
19  business/live/2024/jul/12/pound-hovers-one-yea...  liveblog   
20  business/live/2024/feb/02/ai-jobs-bank-of-engl...  liveblog   
21  business/live/2023/dec/06/elon-musks-x-ai-1bn-...  liveblog   
22  business/live/2024/sep/17/microsoft-share-buyb...  liveblog   
23  australia-news/2024/jan/31/afternoon-update-in...   article   
24  business/live/2024/sep/04/markets-slump-growth...  liveblog   
25  technology/2023/jun/11/falling-funds-and-the-r...   article   
26  business/2024/mar/14/imf-kristalina-georgieva-...   article   
27  business/2024/apr/07/from-hs2-to-the-nhs-brita...   article   
28  business/live/2024/sep/12/john-lewis-partnersh...  liveblog   
29  business/nils-pratley-on-finance/article/2024/...   article   
30  business/article/2024/sep/07/labours-first-job...   article   
31  commentisfree/article/2024/jun/15/labours-choc...   article   
32  business/2024/apr/09/m-and-s-invests-methane-b...   article   
33  world/2024/apr/17/efficient-reliable-and-fragr...   article   
34  business/live/2024/aug/07/uk-house-prices-jump...  liveblog   
35  business/2024/mar/16/sainsburys-grocery-delive...   article   
36  australia-news/article/2024/sep/07/nostalgic-g...   article   
37  business/2024/jan/16/uk-pay-growth-inflation-v...   article   
38  business/live/2024/jul/02/sainsburys-sales-slo...  liveblog   
39  business/2024/apr/25/sainsburys-sales-big-tick...   article   
40  business/live/2024/apr/04/brexit-food-import-c...  liveblog   
41  business/live/2023/may/30/asda-10bn-petrol-sta...  liveblog   
42  politics/article/2024/aug/16/rba-inflation-int...   article   
43  commentisfree/article/2024/aug/25/britain-coul...   article   
44  business/article/2024/sep/08/australian-econom...   article   
45  politics/2024/apr/09/how-realistic-labour-aspi...   article   
46  business/live/2024/jan/10/inflationary-pressur...  liveblog   
47  australia-news/article/2024/jul/16/australias-...   article   
48  business/2024/mar/17/us-small-businesses-hirin...   article   
49  business/2023/oct/26/ecb-keeps-interest-rates-...   article   
50  australia-news/article/2024/jun/19/coalition-a...   article   
51  business/article/2024/jul/21/its-been-raining-...   article   

         sectionId     sectionName        webPublicationDate  \
0         business        Business 2024-08-02 10:15:31+00:00   
1         business        Business 2024-07-12 14:04:03+00:00   
2    commentisfree         Opinion 2024-07-10 15:07:18+00:00   
3         business        Business 2024-08-04 11:02:05+00:00   
4         business        Business 2024-09-01 10:32:29+00:00   
5         business        Business 2024-05-30 14:38:46+00:00   
6         business        Business 2024-08-05 16:45

In [ ]:
topic_model.visualize_barchart(n_words=10, height=400)